In [0]:
!pip install kaggle

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.7/12.7 MB 96.7 MB/s eta 0:00:00
Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
import os

os.environ["KAGGLE_USERNAME"] = "prashansabhatia"
os.environ["KAGGLE_KEY"] = "KGAT_7cdb76b4b41a2dec2cdc2f426b1d8790"

print("Kaggle credentials configured!")

Kaggle credentials configured!


In [0]:
spark.sql("""
CREATE SCHEMA IF NOT EXISTS workspace.ecommerce
""")

DataFrame[]

In [0]:
spark.sql("""
CREATE VOLUME IF NOT EXISTS workspace.ecommerce.ecommerce_data
""")

DataFrame[]

In [0]:
!cd /Volumes/workspace/ecommerce/ecommerce_data && kaggle datasets download -d mkechinov/ecommerce-behavior-data-from-multi-category-store

Dataset URL: https://www.kaggle.com/datasets/mkechinov/ecommerce-behavior-data-from-multi-category-store
License(s): copyright-authors
100%|█████████████████████████████████████▉| 4.29G/4.29G [01:13<00:00, 67.7MB/s]
100%|██████████████████████████████████████| 4.29G/4.29G [01:13<00:00, 62.4MB/s]


In [0]:
!cd /Volumes/workspace/ecommerce/ecommerce_data && unzip -o ecommerce-behavior-data-from-multi-category-store.zip && ls -lh

Archive:  ecommerce-behavior-data-from-multi-category-store.zip
  inflating: 2019-Nov.csv            
  inflating: 2019-Oct.csv            
total 18G
-rwxrwxrwx 1 spark-585ed2b5-37c2-4e7b-9042-4e nogroup 8.4G Jan 14 14:47 2019-Nov.csv
-rwxrwxrwx 1 spark-585ed2b5-37c2-4e7b-9042-4e nogroup 5.3G Jan 14 14:49 2019-Oct.csv
-rwxrwxrwx 1 spark-585ed2b5-37c2-4e7b-9042-4e nogroup 4.3G Jan 14 14:44 ecommerce-behavior-data-from-multi-category-store.zip


In [0]:
!cd /Volumes/workspace/ecommerce/ecommerce_data && rm -f ecommerce-behavior-data-from-multi-category-store.zip && ls -lh

total 14G
-rwxrwxrwx 1 nobody nogroup 8.4G Jan 14 14:47 2019-Nov.csv
-rwxrwxrwx 1 nobody nogroup 5.3G Jan 14 14:49 2019-Oct.csv


In [0]:
%restart_python

In [0]:
df_n = spark.read.csv("/Volumes/workspace/ecommerce/ecommerce_data/2019-Nov.csv")

In [0]:
df = spark.read.csv("/Volumes/workspace/ecommerce/ecommerce_data/2019-Oct.csv")

In [0]:
print(f"October 2019 - Total Events: {df.count():,}")
print("\n" + "="*60)
print("SCHEMA:")
print("="*60)
df.printSchema()

October 2019 - Total Events: 42,448,765

SCHEMA:
root
 |-- _c0: string (nullable = true)
 |-- _c1: string (nullable = true)
 |-- _c2: string (nullable = true)
 |-- _c3: string (nullable = true)
 |-- _c4: string (nullable = true)
 |-- _c5: string (nullable = true)
 |-- _c6: string (nullable = true)
 |-- _c7: string (nullable = true)
 |-- _c8: string (nullable = true)



In [0]:
print("\n" + "="*60)
print("SAMPLE DATA (First 5 rows):")
print("="*60)
df.show(5, truncate=False)


SAMPLE DATA (First 5 rows):
+-----------------------+----------+----------+-------------------+-----------------------------------+--------+------+---------+------------------------------------+
|_c0                    |_c1       |_c2       |_c3                |_c4                                |_c5     |_c6   |_c7      |_c8                                 |
+-----------------------+----------+----------+-------------------+-----------------------------------+--------+------+---------+------------------------------------+
|event_time             |event_type|product_id|category_id        |category_code                      |brand   |price |user_id  |user_session                        |
|2019-10-01 00:00:00 UTC|view      |44600062  |2103807459595387724|NULL                               |shiseido|35.79 |541312140|72d76fde-8bb3-4e00-8c23-a032dfed738c|
|2019-10-01 00:00:00 UTC|view      |3900821   |2053013552326770905|appliances.environment.water_heater|aqua    |33.20 |554748717|9333dfb

In [0]:
events = df

In [0]:
print(f"✅ Ready to go! Loaded {events.count():,} events")
events.show(5)

✅ Ready to go! Loaded 42,448,765 events
+--------------------+----------+----------+-------------------+--------------------+--------+------+---------+--------------------+
|                 _c0|       _c1|       _c2|                _c3|                 _c4|     _c5|   _c6|      _c7|                 _c8|
+--------------------+----------+----------+-------------------+--------------------+--------+------+---------+--------------------+
|          event_time|event_type|product_id|        category_id|       category_code|   brand| price|  user_id|        user_session|
|2019-10-01 00:00:...|      view|  44600062|2103807459595387724|                NULL|shiseido| 35.79|541312140|72d76fde-8bb3-4e0...|
|2019-10-01 00:00:...|      view|   3900821|2053013552326770905|appliances.enviro...|    aqua| 33.20|554748717|9333dfbd-b87a-470...|
|2019-10-01 00:00:...|      view|  17200506|2053013559792632471|furniture.living_...|    NULL|543.10|519107250|566511c2-e2e3-422...|
|2019-10-01 00:00:...|      v

In [0]:
# Show schema
print('Schema:')
events.printSchema()

# Count rows
print(f'Total rows: {events.count():,}')

# Show sample data
print('\nSample data:')
events.show(5, truncate=False)

# Simple aggregation: group by first column (if available)
first_col = events.columns[0] if events.columns else None
if first_col:
    print(f'\nAggregation: count by {first_col}')
    events.groupBy(first_col).count().show(5)
else:
    print('No columns available for aggregation.')

Schema:
root
 |-- _c0: string (nullable = true)
 |-- _c1: string (nullable = true)
 |-- _c2: string (nullable = true)
 |-- _c3: string (nullable = true)
 |-- _c4: string (nullable = true)
 |-- _c5: string (nullable = true)
 |-- _c6: string (nullable = true)
 |-- _c7: string (nullable = true)
 |-- _c8: string (nullable = true)

Total rows: 42,448,765

Sample data:
+-----------------------+----------+----------+-------------------+-----------------------------------+--------+------+---------+------------------------------------+
|_c0                    |_c1       |_c2       |_c3                |_c4                                |_c5     |_c6   |_c7      |_c8                                 |
+-----------------------+----------+----------+-------------------+-----------------------------------+--------+------+---------+------------------------------------+
|event_time             |event_type|product_id|category_id        |category_code                      |brand   |price |user_id  |user

In [0]:
from pyspark.sql.functions import col

# Select specific columns
selected = events.select('_c1', '_c5', '_c6')  # event_type, brand, price
print('Selected columns: event_type, brand, price')
selected.show(5)

# Filter rows where event_type is 'view'
filtered = events.filter(col('_c1') == 'view')
print("Filtered rows where event_type = 'view'")
filtered.show(5)

# Group by brand and count
grouped = filtered.groupBy('_c5').count()
print('Grouped by brand, counted events')
grouped.show(5)

# Order by count descending
ordered = grouped.orderBy(col('count').desc())
print('Ordered by count descending')
ordered.show(5)

Selected columns: event_type, brand, price
+----------+--------+------+
|       _c1|     _c5|   _c6|
+----------+--------+------+
|event_type|   brand| price|
|      view|shiseido| 35.79|
|      view|    aqua| 33.20|
|      view|    NULL|543.10|
|      view|  lenovo|251.74|
+----------+--------+------+
only showing top 5 rows
Filtered rows where event_type = 'view'
+--------------------+----+--------+-------------------+--------------------+--------+-------+---------+--------------------+
|                 _c0| _c1|     _c2|                _c3|                 _c4|     _c5|    _c6|      _c7|                 _c8|
+--------------------+----+--------+-------------------+--------------------+--------+-------+---------+--------------------+
|2019-10-01 00:00:...|view|44600062|2103807459595387724|                NULL|shiseido|  35.79|541312140|72d76fde-8bb3-4e0...|
|2019-10-01 00:00:...|view| 3900821|2053013552326770905|appliances.enviro...|    aqua|  33.20|554748717|9333dfbd-b87a-470...|
|2

In [0]:
# Export the ordered DataFrame to CSV
output_path = "/Volumes/workspace/ecommerce/ecommerce_data/brand_event_counts.csv"
ordered.coalesce(1).write.mode('overwrite').option('header', True).csv(output_path)
print(f"Results exported to {output_path}")

Results exported to /Volumes/workspace/ecommerce/ecommerce_data/brand_event_counts.csv


In [0]:
# Join October and November data on user_id and product_id
join_cols = ['_c2', '_c7']  # product_id, user_id

# Filter for 'view' events in both months
oct_views = events.filter(col('_c1') == 'view')
nov_views = df_n.filter(col('_c1') == 'view')

# Perform inner join
joined = oct_views.join(nov_views, on=[oct_views['_c2'] == nov_views['_c2'], oct_views['_c7'] == nov_views['_c7']], how='inner')

# Select relevant columns from both months
result = joined.select(
    oct_views['_c7'].alias('user_id'),
    oct_views['_c2'].alias('product_id'),
    oct_views['_c0'].alias('oct_event_time'),
    nov_views['_c0'].alias('nov_event_time'),
    oct_views['_c5'].alias('oct_brand'),
    nov_views['_c5'].alias('nov_brand')
)

print('Sample of users who viewed the same product in both October and November:')
result.show(5, truncate=False)

Sample of users who viewed the same product in both October and November:
+---------+----------+-----------------------+-----------------------+---------+---------+
|user_id  |product_id|oct_event_time         |nov_event_time         |oct_brand|nov_brand|
+---------+----------+-----------------------+-----------------------+---------+---------+
|514097469|46800031  |2019-10-21 12:19:55 UTC|2019-11-01 00:29:34 UTC|coolfort |coolfort |
|529214846|1004833   |2019-10-24 02:25:31 UTC|2019-11-01 01:57:59 UTC|samsung  |samsung  |
|548299732|1801995   |2019-10-16 01:54:56 UTC|2019-11-01 02:22:33 UTC|haier    |haier    |
|548299732|1801995   |2019-10-16 01:54:56 UTC|2019-11-01 02:24:14 UTC|haier    |haier    |
|565318484|12711558  |2019-10-30 18:32:38 UTC|2019-11-01 02:30:25 UTC|triangle |triangle |
+---------+----------+-----------------------+-----------------------+---------+---------+
only showing top 5 rows


In [0]:
from pyspark.sql.window import Window
from pyspark.sql.functions import col, to_timestamp, row_number, count

# Filter out header row
filtered_events = events.filter(col('_c0') != 'event_time')

# Prepare data: ensure event_time is timestamp
with_ts = filtered_events.withColumn('event_time_ts', to_timestamp(col('_c0')))

# Define window: partition by user_id, order by event_time
user_window = Window.partitionBy('_c7').orderBy('event_time_ts').rowsBetween(Window.unboundedPreceding, Window.currentRow)

# Calculate running total of events per user
with_running_total = with_ts.withColumn('running_event_count', count('*').over(user_window))

# Show sample for a single user
sample_user = with_running_total.select('_c7').limit(1).collect()[0][0]
print(f"Sample running totals for user_id: {sample_user}")
with_running_total.filter(col('_c7') == sample_user).select('_c0', '_c7', 'running_event_count').show(10)

Sample running totals for user_id: 541312140
+--------------------+---------+-------------------+
|                 _c0|      _c7|running_event_count|
+--------------------+---------+-------------------+
|2019-10-01 00:00:...|541312140|                  1|
|2019-10-01 00:00:...|541312140|                  2|
|2019-10-02 14:30:...|541312140|                  3|
|2019-10-05 14:10:...|541312140|                  4|
|2019-10-05 14:11:...|541312140|                  5|
|2019-10-05 14:12:...|541312140|                  6|
|2019-10-05 14:12:...|541312140|                  7|
|2019-10-05 14:13:...|541312140|                  8|
|2019-10-05 14:13:...|541312140|                  9|
|2019-10-05 14:14:...|541312140|                 10|
+--------------------+---------+-------------------+
only showing top 10 rows


In [0]:
from pyspark.sql.functions import col, to_timestamp, hour, when, count
from pyspark.sql.window import Window

# Filter out header row
filtered_events = events.filter(col('_c0') != 'event_time')

# Create event_hour feature
with_hour = filtered_events.withColumn('event_hour', hour(to_timestamp(col('_c0'))))

# Create is_high_price feature (price > 100)
with_price_flag = with_hour.withColumn('is_high_price', when(col('_c6').cast('float') > 100, 1).otherwise(0))

# Create session_length feature (count of events per user_session)
session_window = Window.partitionBy('_c8')
with_session_length = with_price_flag.withColumn('session_length', count('*').over(session_window))

# Show sample of derived features
with_session_length.select('_c0', '_c1', '_c5', '_c6', 'event_hour', 'is_high_price', '_c8', 'session_length').show(10, truncate=False)

+-----------------------+----+-------+------+----------+-------------+------------------------------------+--------------+
|_c0                    |_c1 |_c5    |_c6   |event_hour|is_high_price|_c8                                 |session_length|
+-----------------------+----+-------+------+----------+-------------+------------------------------------+--------------+
|2019-10-06 14:26:10 UTC|cart|tcl    |135.65|14        |1            |NULL                                |2             |
|2019-10-25 10:36:14 UTC|cart|samsung|246.52|10        |1            |NULL                                |2             |
|2019-10-14 19:03:55 UTC|view|huawei |252.21|19        |1            |00001417-945d-4ab1-a69c-3e6a13b186f2|1             |
|2019-10-22 16:51:37 UTC|view|NULL   |90.09 |16        |0            |00006c6c-799c-4f14-baf2-3ebd863da937|1             |
|2019-10-26 10:51:18 UTC|view|xiaomi |138.74|10        |1            |000089a1-ee47-49e1-9450-91f7c2e3155f|1             |
|2019-10-17 07:3

In [0]:
# Write November data as Delta format to volume (local use only)
nov_delta_path = "/Volumes/workspace/ecommerce/ecommerce_data/nov_delta"
df_n.write.format("delta").mode("overwrite").save(nov_delta_path)
print(f"November data converted to Delta format at {nov_delta_path}")

November data converted to Delta format at /Volumes/workspace/ecommerce/ecommerce_data/nov_delta


In [0]:
%sql
-- SQL: Create Delta table directly from CSV file
DROP TABLE IF EXISTS workspace.ecommerce.nov_delta_sql;
CREATE TABLE workspace.ecommerce.nov_delta_sql
USING DELTA
AS
SELECT * FROM read_files('/Volumes/workspace/ecommerce/ecommerce_data/2019-Nov.csv',
                         format => 'csv',
                         header => true);
-- Table workspace.ecommerce.nov_delta_sql created from CSV using SQL.

num_affected_rows num_inserted_rows

In [0]:
from pyspark.sql.types import StructType, StructField, StringType, FloatType

# Define expected schema for November data
expected_schema = StructType([
    StructField("event_time", StringType(), True),
    StructField("event_type", StringType(), True),
    StructField("product_id", StringType(), True),
    StructField("category_id", StringType(), True),
    StructField("category_code", StringType(), True),
    StructField("brand", StringType(), True),
    StructField("price", FloatType(), True),
    StructField("user_id", StringType(), True),
    StructField("user_session", StringType(), True)
])

# Read November CSV with schema enforcement
df_n_enforced = spark.read.schema(expected_schema).csv("/Volumes/workspace/ecommerce/ecommerce_data/2019-Nov.csv")

# Display schema and sample data to verify enforcement
print("Schema after enforcement:")
df_n_enforced.printSchema()
display(df_n_enforced.limit(5))

Schema after enforcement:
root
 |-- event_time: string (nullable = true)
 |-- event_type: string (nullable = true)
 |-- product_id: string (nullable = true)
 |-- category_id: string (nullable = true)
 |-- category_code: string (nullable = true)
 |-- brand: string (nullable = true)
 |-- price: float (nullable = true)
 |-- user_id: string (nullable = true)
 |-- user_session: string (nullable = true)



event_time event_type product_id category_id category_code brand price user_id user_session event_time event_type product_id category_id category_code brand null user_id user_session 2019-11-01 00:00:00 UTC view 1003461 2053013555631882655 electronics.smartphone xiaomi 489.07 520088904 4d3b30da-a5e4-49df-b1a8-ba5943f1dd33 2019-11-01 00:00:00 UTC view 5000088 2053013566100866035 appliances.sewing_machine janome 293.65 530496790 8e5f4f83-366c-4f70-860e-ca7417414283 2019-11-01 00:00:01 UTC view 17302664 2053013553853497655 null creed 28.31 561587266 755422e7-9040-477b-9bd2-6a6e8fd97387 2019-11-01 00:00:01 UTC view 3601530 2053013563810775923 appliances.kitchen.washer lg 712.87 518085591 3bfb58cd-7892-48cc-8020-2f17e6de6e7f

In [0]:
%sql
-- Insert a duplicate row
INSERT INTO workspace.ecommerce.nov_delta_sql
SELECT * FROM workspace.ecommerce.nov_delta_sql LIMIT 1;

-- Query for duplicates by counting identical rows
SELECT event_time, event_type, product_id, category_id, category_code, brand, price, user_id, user_session, COUNT(*) as duplicate_count
FROM workspace.ecommerce.nov_delta_sql
GROUP BY event_time, event_type, product_id, category_id, category_code, brand, price, user_id, user_session
HAVING COUNT(*) > 1;

event_time event_type product_id category_id category_code brand price user_id user_session duplicate_count 2019-11-17T06:21:30.000Z cart 1004767 2053013555631882655 electronics.smartphone samsung 264.77 535866561 586d877e-70e3-4658-9f4d-4a7e8801a3ef 3 2019-11-20T05:05:46.000Z cart 10300052 2053013553115300101 null bruder 70.09 573745725 cfe31817-4980-4b79-a18a-ffded2a07d07 2 2019-11-20T05:36:21.000Z cart 54100010 2145153815500816706 null fubag 47.11 556724593 e727b2d5-d9e0-46a5-b67e-6aad8e526e6d 3 2019-11-16T14:13:04.000Z cart 1004750 2053013555631882655 electronics.smartphone samsung 193.92 532934894 3eda26ff-e3aa-44f6-8d7e-f0c07fe3c7f2 9 2019-11-17T12:43:30.000Z cart 1005256 2053013555631882655 electronics.smartphone xiaomi 133.59 518622728 5385e5cd-bb8c-4af6-a1f8-d6eca14c25f2 3 2019-11-17T12:59:46.000Z cart 5400104 2053013552989470973 null svc 32.18 514719162 12315191-38cb-4847-80c2-bbf590be0237 2 2019-11-17T11:05:44.000Z cart 1004870 2053013555631882655 electronics.smartphone samsung 298.28 554956601 a72eb1b9-f2a6-4597-a140-8bffa9fed65c 2 2019-11-17T06:40:22.000Z cart 1005205 2053013555631882655 electronics.smartphone oppo 231.64 535755481 bedd377d-48cb-40d9-b48f-2f04db2f0064 3 2019-11-20T06:53:52.000Z cart 22700104 2053013556168753601 null yato 39.3 515830645 8136c74a-e6b4-4984-b799-a88facce91df 2 2019-11-20T09:53:01.000Z cart 3700766 2053013565983425517 appliances.environment.vacuum samsung 136.4 539910091 57e8e1f8-f0e0-4c4b-81dd-abb6c5d57499 17 2019-11-16T12:16:06.000Z cart 3601535 2053013563810775923 appliances.kitchen.washer samsung 386.08 571087358 a0ee79ba-a984-4da2-a180-16bf33ad0872 2 2019-11-16T12:28:12.000Z cart 21404526 2053013561579406073 electronics.clocks casio 25.23 525484136 33c7ab8a-4ffa-4f42-b07c-4e3d02430c22 2 2019-11-17T07:43:25.000Z cart 26400246 2053013563651392361 null null 145.43 512721117 c17a4613-96d3-4772-8340-4c2319185add 3 2019-11-17T08:03:39.000Z cart 3601603 2053013563810775923 appliances.kitchen.washer lg 368.09 513607465 5afb5f02-df82-409f-a7f2-a02f0b94ddee 2 2019-11-17T08:37:42.000Z cart 3600661 2053013563810775923 appliances.kitchen.washer samsung 308.86 545207039 3f91c36a-f953-4cc3-84e6-4c441297ecba 2 2019-11-20T09:17:39.000Z cart 4801583 2053013554658804075 electronics.audio.headphone kingston 61.48 541529961 3d12ada4-126c-9749-5722-830dc0541800 2 2019-11-16T14:53:31.000Z cart 1004956 2053013555631882655 electronics.smartphone xiaomi 372.96 571891679 053afc3e-04cd-4efe-8158-7b51b93eda03 2 2019-11-17T12:07:31.000Z cart 28717686 2053013565782098913 apparel.shoes greyder 77.22 563923105 e076b4e8-5a2c-47bd-b740-01a334c36481 2 2019-11-17T10:33:03.000Z cart 17800166 2053013559868129947 computers.desktop aerocool 167.29 547323325 90692076-4e26-45fd-8bc4-b9e2c91244fd 2 2019-11-17T10:55:57.000Z cart 4000169 2053013566142809077 construction.tools.generator tefal 102.94 517977632 1cc37291-d4c2-4c1a-9e85-5004df68a3ff 2 2019-11-17T08:30:42.000Z cart 1004781 2053013555631882655 electronics.smartphone huawei 262.5 546286713 5a58d8ba-1e6e-46c0-b823-49bf88c4e9b4 2 2019-11-20T11:33:32.000Z cart 3601438 2053013563810775923 appliances.kitchen.washer beko 215.92 552832537 e10a7e59-b7d3-40cb-a027-d565248e0fdc 2 2019-11-17T11:28:58.000Z cart 5701166 2053013553970938175 auto.accessories.player null 144.12 515946814 a58bdaf0-fb58-4cb5-9a61-d8673152945a 2 2019-11-17T11:56:21.000Z cart 4700651 2053013560899928785 auto.accessories.videoregister anytek 100.39 568540921 661362c9-f825-486c-b3d4-68824543e924 2 2019-11-17T12:36:31.000Z cart 2900958 2053013554776244595 appliances.kitchen.microwave arg 59.18 549135719 3d8a7f4f-09af-40a4-8b91-cc325fba4609 2 2019-11-21T10:10:33.000Z cart 12713435 2053013553559896355 null tunga 37.32 513182991 a216cc3b-f33b-471c-acf7-7ad43b6bafe9 2 2019-11-21T11:54:42.000Z cart 1004856 2053013555631882655 electronics.smartphone samsung 126.82 541292753 eabe03db-419b-4b61-befa-8e460b60f794 6 2019-11-21T14:07:33.000Z cart 12703015 2053013553559896355 null cordiant 42.99 514901287 ac14dd47-b0

In [0]:
from delta.tables import DeltaTable

# Load Delta table
delta_table_path = "/Volumes/workspace/ecommerce/ecommerce_data/nov_delta"
delta_table = DeltaTable.forPath(spark, delta_table_path)
delta_df = delta_table.toDF()

print("Delta Table Schema:")
delta_df.printSchema()
print("Delta Table Columns:", delta_df.columns)
print("Delta Table Sample:")
delta_df.show(5)

print("\nEnforced DataFrame Schema:")
df_n_enforced.printSchema()
print("Enforced DataFrame Columns:", df_n_enforced.columns)
print("Enforced DataFrame Sample:")
df_n_enforced.show(5)

# Check for column name and type mismatches
delta_cols = set(delta_df.columns)
enforced_cols = set(df_n_enforced.columns)
print("\nColumns in Delta Table but not in Enforced DataFrame:", delta_cols - enforced_cols)
print("Columns in Enforced DataFrame but not in Delta Table:", enforced_cols - delta_cols)

Delta Table Schema:
root
 |-- _c0: string (nullable = true)
 |-- _c1: string (nullable = true)
 |-- _c2: string (nullable = true)
 |-- _c3: string (nullable = true)
 |-- _c4: string (nullable = true)
 |-- _c5: string (nullable = true)
 |-- _c6: string (nullable = true)
 |-- _c7: string (nullable = true)
 |-- _c8: string (nullable = true)

Delta Table Columns: ['_c0', '_c1', '_c2', '_c3', '_c4', '_c5', '_c6', '_c7', '_c8']
Delta Table Sample:
+--------------------+----------+----------+-------------------+--------------------+------+------+---------+--------------------+
|                 _c0|       _c1|       _c2|                _c3|                 _c4|   _c5|   _c6|      _c7|                 _c8|
+--------------------+----------+----------+-------------------+--------------------+------+------+---------+--------------------+
|          event_time|event_type|product_id|        category_id|       category_code| brand| price|  user_id|        user_session|
|2019-11-01 00:00:...|      vi

In [0]:
from pyspark.sql.types import StructType, StructField, StringType, FloatType
from delta.tables import DeltaTable
from pyspark.sql.functions import col

# Define expected schema for November data
expected_schema = StructType([
    StructField("event_time", StringType(), True),
    StructField("event_type", StringType(), True),
    StructField("product_id", StringType(), True),
    StructField("category_id", StringType(), True),
    StructField("category_code", StringType(), True),
    StructField("brand", StringType(), True),
    StructField("price", FloatType(), True),
    StructField("user_id", StringType(), True),
    StructField("user_session", StringType(), True)
])

# Read November CSV with schema enforcement and skip header
df_n_enforced = spark.read.schema(expected_schema).option("header", True).csv("/Volumes/workspace/ecommerce/ecommerce_data/2019-Nov.csv")

# Overwrite and recreate Delta table with correct schema
nov_delta_path = "/Volumes/workspace/ecommerce/ecommerce_data/nov_delta"
df_n_enforced.write.format("delta").mode("overwrite").option("overwriteSchema", "true").save(nov_delta_path)

# Load Delta table
nov_delta = DeltaTable.forPath(spark, nov_delta_path)

# Prepare new data for incremental merge (simulate with same DataFrame for demo)
new_data = df_n_enforced

# Define merge condition on all columns
merge_condition = " AND ".join([
    f"target.{col} = source.{col}" for col in new_data.columns
])

# Perform incremental merge: insert only new rows
nov_delta.alias("target").merge(
    new_data.alias("source"),
    merge_condition
).whenNotMatchedInsertAll().execute()

print("✅ Delta table recreated and incremental merge complete. No errors.")

✅ Delta table recreated and incremental merge complete. No errors.


In [0]:
from delta.tables import DeltaTable

nov_delta_path = "/Volumes/workspace/ecommerce/ecommerce_data/nov_delta"
delta_table = DeltaTable.forPath(spark, nov_delta_path)

# List all historical versions
history_df = delta_table.history()
display(history_df)

# Query a specific historical version (e.g., version 0)
version_0_df = spark.read.format("delta").option("versionAsOf", 0).load(nov_delta_path)
display(version_0_df.limit(5))

version timestamp userId userName operation operationParameters job notebook clusterId readVersion isolationLevel isBlindAppend operationMetrics userMetadata engineInfo 5 2026-01-14T17:13:34.000Z 78514223462737 prashu0705@gmail.com MERGE Map(predicate -> ["(((((event_time#18472 = event_time#18297) AND (event_type#18473 = event_type#18298)) AND (product_id#18474 = product_id#18299)) AND ((category_id#18475 = category_id#18300) AND (category_code#18476 = category_code#18301))) AND (((brand#18477 = brand#18302) AND (price#18478 = price#18303)) AND ((user_id#18479 = user_id#18304) AND (user_session#18480 = user_session#18305))))"], clusterBy -> [], matchedPredicates -> [], statsOnLoad -> false, notMatchedBySourcePredicates -> [], notMatchedPredicates -> [{"actionType":"insert"}]) null List(3828226002073275) 0114-152334-8ex3s4er-v2n 4 WriteSerializable false Map(numTargetRowsCopied -> 0, numTargetRowsDeleted -> 0, numTargetFilesAdded -> 147, numTargetBytesAdded -> 1443859507, numTargetBytesRemoved -> 0, numTargetDeletionVectorsAdded -> 0, numTargetRowsMatchedUpdated -> 0, executionTimeMs -> 68413, materializeSourceTimeMs -> 5, numTargetRowsInserted -> 25412415, numTargetRowsMatchedDeleted -> 0, numTargetDeletionVectorsUpdated -> 0, scanTimeMs -> 0, numTargetRowsUpdated -> 0, numOutputRows -> 25412415, numTargetDeletionVectorsRemoved -> 0, numTargetRowsNotMatchedBySourceUpdated -> 0, numTargetChangeFilesAdded -> 0, numSourceRows -> 67501979, numTargetFilesRemoved -> 0, numTargetRowsNotMatchedBySourceDeleted -> 0, rewriteTimeMs -> 68326) null Databricks-Runtime/17.3.x-aarch64-photon-scala2.13 4 2026-01-14T17:12:25.000Z 78514223462737 prashu0705@gmail.com WRITE Map(mode -> Overwrite, statsOnLoad -> false, partitionBy -> []) null List(3828226002073275) 0114-152334-8ex3s4er-v2n 3 WriteSerializable false Map(numFiles -> 68, numRemovedFiles -> 68, numRemovedBytes -> 2586091812, numDeletionVectorsRemoved -> 0, numOutputRows -> 67501979, numOutputBytes -> 2584417797) null Databricks-Runtime/17.3.x-aarch64-photon-scala2.13 3 2026-01-14T15:53:07.000Z 78514223462737 prashu0705@gmail.com WRITE Map(mode -> Overwrite, statsOnLoad -> false, partitionBy -> []) null List(3828226002073275) 0114-152334-8ex3s4er-v2n 2 WriteSerializable false Map(numFiles -> 68, numRemovedFiles -> 68, numRemovedBytes -> 2586091812, numDeletionVectorsRemoved -> 0, numOutputRows -> 67501980, numOutputBytes -> 2586091812) null Databricks-Runtime/17.3.x-aarch64-photon-scala2.13 2 2026-01-14T15:50:27.000Z 78514223462737 prashu0705@gmail.com WRITE Map(mode -> Overwrite, statsOnLoad -> false, partitionBy -> []) null List(3828226002073275) 0114-152334-8ex3s4er-v2n 1 WriteSerializable false Map(numFiles -> 68, numRemovedFiles -> 68, numRemovedBytes -> 2586091812, numDeletionVectorsRemoved -> 0, numOutputRows -> 67501980, numOutputBytes -> 2586091812) null Databricks-Runtime/17.3.x-aarch64-photon-scala2.13 1 2026-01-14T15:48:53.000Z 78514223462737 prashu0705@gmail.com WRITE Map(mode -> Overwrite, statsOnLoad -> false, partitionBy -> []) null List(3828226002073275) 0114-152334-8ex3s4er-v2n 0 WriteSerializable false Map(numFiles -> 68, numRemovedFiles -> 68, numRemovedBytes -> 2586091812, numDeletionVectorsRemoved -> 0, numOutputRows -> 67501980, numOutputBytes -> 2586091812) null Databricks-Runtime/17.3.x-aarch64-photon-scala2.13 0 2026-01-14T15:46:15.000Z 78514223462737 prashu0705@gmail.com WRITE Map(mode -> Overwrite, statsOnLoad -> false, partitionBy -> []) null List(3828226002073275) 0114-152334-8ex3s4er-v2n null WriteSerializable false Map(numFiles -> 68, numRemovedFiles -> 0, numRemovedBytes -> 0, numDeletionVectorsRemoved -> 0, numOutputRows -> 67501980, numOutputBytes -> 2586091812) null Databricks-Runtime/17.3.x-aarch64-photon-scala2.13

_c0 _c1 _c2 _c3 _c4 _c5 _c6 _c7 _c8 event_time event_type product_id category_id category_code brand price user_id user_session 2019-11-01 00:00:00 UTC view 1003461 2053013555631882655 electronics.smartphone xiaomi 489.07 520088904 4d3b30da-a5e4-49df-b1a8-ba5943f1dd33 2019-11-01 00:00:00 UTC view 5000088 2053013566100866035 appliances.sewing_machine janome 293.65 530496790 8e5f4f83-366c-4f70-860e-ca7417414283 2019-11-01 00:00:01 UTC view 17302664 2053013553853497655 null creed 28.31 561587266 755422e7-9040-477b-9bd2-6a6e8fd97387 2019-11-01 00:00:01 UTC view 3601530 2053013563810775923 appliances.kitchen.washer lg 712.87 518085591 3bfb58cd-7892-48cc-8020-2f17e6de6e7f

In [0]:
nov_delta = DeltaTable.forPath(spark, nov_delta_path)

# Optimize table for performance
spark.sql("OPTIMIZE delta.`/Volumes/workspace/ecommerce/ecommerce_data/nov_delta`")

# Clean old files (vacuum with default retention)
nov_delta.vacuum()

In [0]:
from pyspark.sql.functions import col

# Map descriptive column names to generic Delta table column names
column_map = {
    "event_time": "_c0",
    "event_type": "_c1",
    "product_id": "_c2",
    "category_id": "_c3",
    "category_code": "_c4",
    "brand": "_c5",
    "price": "_c6",
    "user_id": "_c7",
    "user_session": "_c8"
}

df_n_renamed = df_n_enforced.select([col(orig).alias(new) for orig, new in column_map.items()])

In [0]:
print("Renamed DataFrame Columns:", df_n_renamed.columns)
df_n_renamed.show(5)

Renamed DataFrame Columns: ['_c0', '_c1', '_c2', '_c3', '_c4', '_c5', '_c6', '_c7', '_c8']
+--------------------+----+--------+-------------------+--------------------+------+------+---------+--------------------+
|                 _c0| _c1|     _c2|                _c3|                 _c4|   _c5|   _c6|      _c7|                 _c8|
+--------------------+----+--------+-------------------+--------------------+------+------+---------+--------------------+
|2019-11-01 00:00:...|view| 1003461|2053013555631882655|electronics.smart...|xiaomi|489.07|520088904|4d3b30da-a5e4-49d...|
|2019-11-01 00:00:...|view| 5000088|2053013566100866035|appliances.sewing...|janome|293.65|530496790|8e5f4f83-366c-4f7...|
|2019-11-01 00:00:...|view|17302664|2053013553853497655|                NULL| creed| 28.31|561587266|755422e7-9040-477...|
|2019-11-01 00:00:...|view| 3601530|2053013563810775923|appliances.kitche...|    lg|712.87|518085591|3bfb58cd-7892-48c...|
|2019-11-01 00:00:...|view| 1004775|205301355563

In [0]:
# 3-Layer Architecture: Bronze, Silver, Gold

# Bronze Layer: Raw Ingestion
bronze_path = "/Volumes/workspace/ecommerce/ecommerce_data/bronze"
df_n_enforced.write.format("delta").mode("overwrite").save(bronze_path)
bronze_df = spark.read.format("delta").load(bronze_path)

# Silver Layer: Cleaning & Validation
from pyspark.sql.functions import col

silver_df = bronze_df.filter(
    (col("event_time").isNotNull()) &
    (col("event_type").isin("view", "cart", "purchase")) &
    (col("product_id").isNotNull()) &
    (col("price").cast("float") > 0)
)
silver_path = "/Volumes/workspace/ecommerce/ecommerce_data/silver"
silver_df.write.format("delta").mode("overwrite").save(silver_path)

# Gold Layer: Business Aggregates (e.g., total purchases per brand)
gold_df = silver_df.filter(col("event_type") == "purchase") \
    .groupBy("brand") \
    .agg({"price": "sum", "*": "count"}) \
    .withColumnRenamed("sum(price)", "total_sales") \
    .withColumnRenamed("count(1)", "purchase_count")
gold_path = "/Volumes/workspace/ecommerce/ecommerce_data/gold"
gold_df.write.format("delta").mode("overwrite").save(gold_path)

# Display Gold Layer
display(gold_df)

brand total_sales purchase_count millionaire 9262.089706420898 121 global 23.03999948501587 5 coolfort 380.84000396728516 5 gulliver 174.40000247955322 4 xing 6186.040023803711 33 ubisoft 5924.049958229065 223 lonex 836.5700073242188 2 patriot 3753.759998321533 55 ecocool 9678.109962463379 105 sordiant 5323.699962615967 99 rimax 5151.22998046875 15 wallberry 537.6499967575073 43 didistyle 579.1500091552734 15 remington 39836.83985233307 652 burton 23333.4497756958 92 ecotex 1427.8600015640259 54 casper 7073.9300537109375 63 lancome 14394.480132102966 195 bellamebel 14429.259643554688 14 lumene 443.75999689102173 34 salvatoreferragamo 487.010009765625 7 henglei 144.67000198364258 6 bartek 5275.599960327148 67 elizavecca 501.75000381469727 38 rosa 2538.780002593994 41 schecter 1579.6000061035156 4 lcf 107.96000003814697 7 marshall 30004.429607391357 255 tpmaster 205.9000015258789 10 skad 115344.12014770508 510 shua 4015.550048828125 3 ivt 1052.290002822876 27 karaja 112.49000072479248 6 husqvarna 7907.420166015625 19 brizoll 88.35999870300293 3 willmark 14000.369894981384 660 milavitsa 1353.6300029754639 50 tecno 9157.600051879883 86 ersport 22829.96006011963 172 grohe 6491.460090637207 43 travellight 591.5099945068359 9 daisy 5748.779998779297 40 haro 3431.009994506836 11 avene 765.5300054550171 40 babor 3935.2499923706055 62 focal 3502.760066986084 23 riviera 8443.970031738281 17 bradex 1174.7999992370605 53 trebl 15581.7200050354 204 carver 3900.6999168395996 24 ballu 30432.459959983826 647 gipfel 5601.500032424927 49 hjc 4015.5699157714844 17 null 1.1025718794894576E7 73273 a-case 808.3200044631958 94 babyzz 452.0 3 activision 1684.2499885559082 32 robertobravo 83102.47050476074 82 kugoo 24410.399993896484 55 orium 6126.779968261719 19 dior 56479.060485839844 443 stryj 82.33999633789062 1 longstyle 2061.8099670410156 9 kristal 21354.380111694336 100 aoteli 7646.0200119018555 169 creed 81013.37972640991 403 visavis 276.459997177124 27 farroad 13675.580043792725 236 total 10623.24997806549 260 epr 11789.26010131836 32 murager 2033.4999389648438 16 powerman 92.77000045776367 2 canon 511642.10769081116 1097 clarion 128.6699981689453 2 sms 329.2799987792969 32 fisherman 471.16999435424805 8 jetair 2370.97998046875 11 netechnics 55065.19873046875 67 norfin 3851.9100017547607 74 babylock 9875.519897460938 6 anahickmann 151.61000061035156 1 nikotex 809.0600128173828 7 hauck 573.5 2 buggy 9416.579971313477 51 peavey 13429.590084075928 37 king 18859.339920043945 133 casada 83644.75894927979 139 granicom 358.310001373291 6 tyrex 22219.890075683594 88 cenmax 6034.020057678223 86 swat 10212.219953536987 162 dickie 111.06000137329102 6 elite 76.20999956130981 13 shagovita 2809.2999572753906 31 porsche 1132.56005859375 8 metabo 11844.99003982544 37 strobbs 21347.340259552002 356 aiko 3381.0499954223633 39 casio 313320.9410009384 3523 horizont 22855.08002090454 189 x-digital 124.98999977111816 4 remax 2932.7099606990814 121 luxell 2893.429998397827 42 tomford 2052.529983520508 32 kingston 65117.130309820175 1387 pituso 12800.589962005615 128 haier 1110829.0417556763 3847 evrodetal 4556.089935302734 21 versace 81352.01960754395 876 moxom 126.57999610900879 4 teka 1573.710048675537 5 selby 7303.089878082275 172 petek 8923.579996109009 128 samsung 5.4869880827870846E7 200027 enlightenbrick 2.9100000858306885 3 epson 342218.5304145813 1475 cybex 61296.69038391113 89 vako 3767.9399795532227 43 delux 1837.3200087547302 136 ducray 204.63999366760254 9 versale 12007.909971237183 81 kettler 4162.239990234375 4 snowcap 1485.620044708252 19 rusgoldart 61179.75038909912 251 s.a.n. 849.8600330352783 27 solite 2177.6700134277344 22 prestigio 61707.800365924835 1217 cordiant 787330.8589115143 16983 hankook 27324.609867095947 308 mbs 2486.7799758911133 24 allocacoc 21.47000026702881 2 boneco 4450.479949951172 29 seagate 13560.060073852539 184 eltempo 6884.729820251465 85 barbie 1030.0100002288818 36 payot 747.629997253418 14 rockforce 2257.5100135803223 27